In [21]:
import pandas as pd
import plotly.express as px
import numpy as np
from us_state import state_to_abbrev

# Electric Vehicle Population Size by County
Plot heat map of electric vehicles using [`Electric_Vehicle_Population_Size_History_By_County.csv`](https://www.autosinnovate.org/resources/electric-vehicle-sales-dashboard).

## Auxiliary Datasets:
From [census.gov](census.gov) webistes.
 - [`2023_Gaz_counties_national.txt`](https://www2.census.gov/geo/docs/maps-data/data/gazetteer/2023_Gazetteer/2023_Gaz_counties_national.zip): location (lat/long) and area of each county
 - [`co-est2022-pop.xlsx`](https://www2.census.gov/programs-surveys/popest/tables/2020-2022/counties/totals/co-est2022-pop.xlsx): population by county


In [2]:
# locations to csv
new_csv = []

with open('data/2023_Gaz_counties_national.txt', 'r') as in_file:
    lines = (line.split("\t") for line in in_file if line)
    lines.__next__()
    for line in lines:
        county = line[3].replace(" County", "")
        state = line[0]
        area = int(float(line[6])+float(line[7]))
        lat = float(line[8])
        lon = float(line[9])
        new_csv.append([','.join([county, state]), area, lat, lon])

new_csv = pd.DataFrame(new_csv, columns=['county', 'area', 'lat', 'lon'])
new_csv.to_csv('data/county_area.csv', index=False)

In [3]:
# clean population data
pop = pd.read_csv('data/co-est2022-pop.csv')
new_csv = []

# remove period before every county name
for i in range(len(pop)):
    county, state = pop['Geographic Area'][i].replace('.', '').split(', ')
    county = county.replace(' County', '')
    new_csv = new_csv + [[','.join([county, state_to_abbrev[state]]), pop['2022'][i].replace(',', '')]]

new_csv = pd.DataFrame(new_csv, columns=['county', 'population'])
new_csv.to_csv('data/county_pop.csv', index=False)


In [129]:
ev_pop_large = pd.read_csv('data/Electric_Vehicle_Population_Size_History_By_County.csv')
ev_pop = pd.DataFrame()
ev_pop['county'] = ev_pop_large['County']+','+ev_pop_large['State']
ev_pop['ev'] = ev_pop_large['Electric Vehicle (EV) Total']
ev_pop['non_ev'] = ev_pop_large['Non-Electric Vehicle Total']
ev_pop['total'] = ev_pop_large['Total Vehicles']
ev_pop['percent_ev'] = ev_pop_large['Percent Electric Vehicles']

county_loc = pd.read_csv('data/county_area.csv')
county_pop = pd.read_csv('data/county_pop.csv')


In [130]:
all_map = pd.merge(ev_pop, county_loc, on='county')
all_map = pd.merge(all_map, county_pop, on='county')

In [33]:
max(all_map.area/min(all_map.area))

773.2692307692307

In [123]:
zoom = 2.5
radii = np.log(all_map.total)*2.5/zoom
radii[radii < 1] = 1
print(all_map[np.max(all_map.total) == all_map.total])

       county     ev   non_ev    total  percent_ev  area        lat  \
7673  King,WA  31856  1400370  1432226        2.22  2307  47.490552   

             lon  population  
7673 -121.833977     2266789  


In [132]:
# plot heatmap for percentage of electric vehicles
fig = px.density_mapbox(all_map, lat='lat', lon='lon', z='percent_ev', radius=radii,
                        center=dict(lat=38, lon=-93.7129), zoom=2.5,
                        mapbox_style="open-street-map",
                        hover_data=['county', 'area', 'percent_ev', 'population'],
                        labels={'percent_ev':'Percent Electric Vehicles', 'area':'Area (sq mi)', 'population':'Population', 'county':'County'},
                        color_continuous_scale=px.colors.sequential.Viridis,
                        title='Percentage of Electric Vehicles by County in the US')

fig.show()

In [133]:
# filter by washington
wa_map = all_map[all_map['county'].str.endswith('WA')]
wa_radii = np.log(wa_map.total)*2
wa_radii[wa_radii < 1] = 1
print(max(wa_map.percent_ev))

fig = px.density_mapbox(wa_map, lat='lat', lon='lon', z='percent_ev', radius=wa_radii,
                        center=dict(lat=47.7511, lon=-120.7401), zoom=5,
                        mapbox_style="open-street-map",
                        hover_data=['county', 'area', 'percent_ev', 'population'],
                        labels={'percent_ev':'Percent Electric Vehicles', 'area':'Area (sq mi)', 'population':'Population', 'county':'County'},
                        color_continuous_scale=px.colors.sequential.Viridis,
                        title='Percentage of Electric Vehicles by County in Washington',
                        range_color=[0, 100])

fig.show()


4.72
